# Initial Imports

In [46]:
from bigdata_a3_utils import *
import shutil
import os
from pathlib import Path
import logging
import tarfile

In [47]:
cache_dir = get_cache_directory()

[INFO] Current cache directory: C:\Users\HomeUser\.cache\huggingface\datasets
[NOTE] To use a custom cache directory, set HF_DATASETS_CACHE before importing datasets.
Example:
    import os
    os.environ['HF_DATASETS_CACHE'] = 'C:\\your\\custom\\path'
    from datasets import load_dataset



In [48]:
default_cache_dir = default_cache_path()

[INFO] Your default cache path: "C:\Users\HomeUser\.cache\huggingface\datasets"


# Checking availble disk space
- Files could also be stored on external drive
- Simply change file path in save_path variable

In [49]:
# Get the disk where your cache directory is located
cache_path = cache_dir
drive = os.path.splitdrive(cache_path)[0]

# Get disk usage statistics
total, used, free = shutil.disk_usage(drive)

# Convert to GB for easier reading
total_gb = total / (1024**3)
used_gb = used / (1024**3)
free_gb = free / (1024**3)

print(f"Drive {drive}:")
print(f"Total: {total_gb:.2f} GB")
print(f"Used: {used_gb:.2f} GB")
print(f"Free: {free_gb:.2f} GB")

# Check if you have enough space (e.g., 220GB to be safe)
required_space = 220  # GB
if free_gb > required_space:
    print(f"✅ You have enough space for the 200GB dataset (with some buffer)")
else:
    print(f"❌ Not enough space! You need at least {required_space} GB, but only have {free_gb:.2f} GB free")
    print(f"Consider setting a custom cache directory on a drive with more space")

Drive C::
Total: 952.94 GB
Used: 640.28 GB
Free: 312.66 GB
✅ You have enough space for the 200GB dataset (with some buffer)


# Division of categories into subsets per person:


In [50]:
subset_sizes = [11, 11, 12]  # Define the sizes of each subset

# Create subsets
subsets = []
start_index = 0
for size in subset_sizes:
    subsets.append(VALID_CATEGORIES[start_index:start_index + size])
    start_index += size

# Unpack the subsets into individual variables
kailash_subset, saeed_subset, johnny_subset = subsets

print(f"Subset list: {subsets}")
print(f"Length: {len(VALID_CATEGORIES)}")
# Output the subsets


Subset list: [['All_Beauty', 'Amazon_Fashion', 'Appliances', 'Arts_Crafts_and_Sewing', 'Automotive', 'Baby_Products', 'Beauty_and_Personal_Care', 'Books', 'CDs_and_Vinyl', 'Cell_Phones_and_Accessories', 'Clothing_Shoes_and_Jewelry'], ['Digital_Music', 'Electronics', 'Gift_Cards', 'Grocery_and_Gourmet_Food', 'Handmade_Products', 'Health_and_Household', 'Health_and_Personal_Care', 'Home_and_Kitchen', 'Industrial_and_Scientific', 'Kindle_Store', 'Magazine_Subscriptions'], ['Movies_and_TV', 'Musical_Instruments', 'Office_Products', 'Patio_Lawn_and_Garden', 'Pet_Supplies', 'Software', 'Sports_and_Outdoors', 'Subscription_Boxes', 'Tools_and_Home_Improvement', 'Toys_and_Games', 'Video_Games', 'Unknown']]
Length: 34


# Setting up log directory and logging system
- Used for proof of file acquisition

In [51]:
log_dir = Path("logs")
log_dir.mkdir(parents=True, exist_ok=True)

logging.basicConfig(
    filename=log_dir / 'data_acquisition.log',
    level=logging.INFO,
    format='%(asctime)s - %(levelname)s - %(message)s'
)

# Error handling:
- In the event of an issue where the folder was not dowloaded properly
- In the event of a issue with preprocessing any particular category (OS error, Permissions error, Temp file being deleted before full extraction) it is likely the initial download was corrupted by some means. As such simply redownload via the last cell, again specifying the failed category

The following function:
- Verifies if a compressed file (tar.gz, zip, etc.) is valid and not corrupted.
- Accepts a path to the compressed file (file_path)
- Returns true if the file is valid, false otherwise

In [52]:
def verify_compressed_file(file_path):
    file_path = Path(file_path)
    
    if not file_path.exists():
        print(f"Error: File does not exist: {file_path}")
        logging.error(f"Error: File does not exist: {file_path}")
        return False
    
    try:
        if file_path.name.endswith('.tar.gz'):
            # Test if tar.gz file is valid
            with tarfile.open(file_path, 'r:gz') as tar:
                # Just check the integrity by attempting to list contents
                tar.getnames()
                print(f"✓ Verified {file_path} is a valid tar.gz file")
                logging.info(f"Verified {file_path} is a valid tar.gz file")
                return True
        else:
            print(f"Error: Unsupported file format for {file_path}")
            logging.error(f"Error: Unsupported file format for {file_path}")
            return False
    except Exception as e:
        print(f"Error verifying {file_path}: {str(e)}")
        logging.error(f"Error verifying {file_path}: {str(e)}")
        return False


# Downloading the folders and metadata
- Just change the file path in save_path accordingly to where you want it stored
- VALID_CATEGORIES will download all metadata and review data for all 34 categories, otherwise choose a subset from above to work with. 

In [53]:
save_path = Path(r"D:\\COMP3610A3")
save_path.mkdir(parents=True, exist_ok=True)

for category in johnny_subset:
    logging.info(f"n------Processing {category}------")
    print(f"\n------Processing {category}------")

    download_all_amazon_reviews(base_save_path=save_path, 
                                categories=[category], compress=False)

    review_folder = save_path / f"raw_review_{category}"
    metadata_folder = save_path / f"raw_meta_{category}"

    if review_folder.exists() and not review_folder.with_suffix('.tar.gz').exists():
        compressed = compress_folder(review_folder, 
                                        compression_format="gz", 
                                        level=6)
        
        logging.info(f"Compressed reviews to: {compressed}")
        print(f"Compressed reviews to: {compressed}")

    if metadata_folder.exists() and not metadata_folder.with_suffix('.tar.gz').exists():
        compressed = compress_folder(metadata_folder, 
                                        compression_format="gz", 
                                        level=6)
        
        logging.info(f"Compressed metadata to: {compressed}")
        print(f"Compressed metadata to: {compressed}")

    review_archive = review_folder.with_suffix('.tar.gz')
    metadata_archive = metadata_folder.with_suffix('.tar.gz')
    
    verify_compressed_file(review_archive)
    verify_compressed_file(metadata_archive)
    delete_cache_directory()



------Processing Movies_and_TV------
[SKIP] raw_review_Movies_and_TV already exists
[SKIP] raw_meta_Movies_and_TV already exists
✅ Processing Movies_and_TV

🎉 Download summary:
  - Successfully processed: 1/1 categories
✓ Verified D:\COMP3610A3\raw_review_Movies_and_TV.tar.gz is a valid tar.gz file
✓ Verified D:\COMP3610A3\raw_meta_Movies_and_TV.tar.gz is a valid tar.gz file
[INFO] Deleting Hugging Face cache at: C:\Users\HomeUser\.cache\huggingface\datasets
[WARNING] Cache directory does not exist: C:\Users\HomeUser\.cache\huggingface\datasets

------Processing Musical_Instruments------
[SKIP] raw_review_Musical_Instruments already exists
[SKIP] raw_meta_Musical_Instruments already exists
✅ Processing Musical_Instruments

🎉 Download summary:
  - Successfully processed: 1/1 categories
✓ Verified D:\COMP3610A3\raw_review_Musical_Instruments.tar.gz is a valid tar.gz file
✓ Verified D:\COMP3610A3\raw_meta_Musical_Instruments.tar.gz is a valid tar.gz file
[INFO] Deleting Hugging Face cach

Generating full split: 0 examples [00:00, ? examples/s]

⠋ Processing Office_Products 

Generating full split: 8920 examples [00:00, 84888.95 examples/s]

⠹ Processing Office_Products 

...

Saving the dataset (18/19 shards): 100%|█████████▉| 26930138/26982256 [01:00<00:00, 555112.84 examples/s]

⠇ Processing Tools_and_Home_Improvement 

Saving the dataset (19/19 shards): 100%|██████████| 26982256/26982256 [01:00<00:00, 445486.02 examples/s]


[DONE] raw_review_Tools_and_Home_Improvement downloaded


KeyboardInterrupt: 

# Note
- the cell below is the one you would use to redownload any specific category that failed during initial download or if OS error, permissions error, file locking error

In [ ]:
save_path = Path(r"D:\BigData")
save_path.mkdir(parents=True, exist_ok=True)
# category = ""
remaining= ["Electronics", "Kindle_Store", "Movies_and_TV", 
            "Sports_and_Outdoors", "Unknown"
            ]

for category in remaining:
    logging.info(f"n------Processing {category}------")
    print(f"\n------Processing {category}------")

    download_all_amazon_reviews(base_save_path=save_path, 
                                categories=[category], compress=False)

    review_folder = save_path / f"raw_review_{category}"
    metadata_folder = save_path / f"raw_meta_{category}"

    if review_folder.exists():
        compressed = compress_folder(review_folder, 
                                        compression_format="gz", 
                                        level=6)
        
        logging.info(f"Compressed reviews to: {compressed}")
        print(f"Compressed reviews to: {compressed}")

    if metadata_folder.exists():
        compressed = compress_folder(metadata_folder, 
                                        compression_format="gz", 
                                        level=6)
        
        logging.info(f"Compressed metadata to: {compressed}")
        print(f"Compressed metadata to: {compressed}")

    verify_compressed_file(review_folder)
    verify_compressed_file(metadata_folder) 